In [14]:
from typing import Iterator, List, Dict
import torch
import torch.optim as optim
import numpy as np
import allennlp
from allennlp.data import Instance
from allennlp.data.fields import TextField, SequenceLabelField
from allennlp.data.dataset_readers import DatasetReader
from allennlp.common.file_utils import cached_path
from allennlp.data.token_indexers import TokenIndexer, SingleIdTokenIndexer
from allennlp.data.tokenizers import Token
from allennlp.data.vocabulary import Vocabulary
from allennlp.models import Model
from allennlp.modules.text_field_embedders import TextFieldEmbedder, BasicTextFieldEmbedder
from allennlp.modules.token_embedders import Embedding
from allennlp.modules.seq2seq_encoders import Seq2SeqEncoder, PytorchSeq2SeqWrapper
from allennlp.nn.util import get_text_field_mask, sequence_cross_entropy_with_logits
from allennlp.training.metrics import CategoricalAccuracy
from allennlp.data.iterators import BucketIterator
from allennlp.training.trainer import Trainer
from allennlp.predictors import SentenceTaggerPredictor
from dataset import BioMedReader
from allennlp.models.coreference_resolution.coref import CoreferenceResolver
torch.manual_seed(1)

#-----------------------------------dataset creation-------------------------------
max_span_width = 7
reader = BioMedReader(max_span_width)
train_dataset = reader.read("/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN")

validation_dataset = reader.read("/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST")



0it [00:00, ?it/s]

2it [00:00, 10.38it/s]

/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/XML/01b14603-8f29-4fa3-8d7e-9d523f802e0b.xml
['758-797']
['633-644']
['951-957']
['861-871']
['875-887']
['2454-2461']
['2466-2472']
['3217-3263']
['3181-3188']
['3333-3344']
['3514-3520']
['3526-3536']
['3540-3552']
['3575-3585']
['3635-3641']
['3711-3722']
['3755-3765']
['3916-3928']
['3959-3965']
['4106-4121']
['4123-4135']
['4140-4152']
['4201-4207']
['4217-4227']
['4231-4243']
['4420-4426']
['4431-4437']
['4727-4733']
['4739-4747']
['4353-4398']
['1380-1387']
['1404-1411']
['1522-1529']
['1554-1561']
['4492-4500']
['4618-4628']
['4689-4697']
['0-6']
['95-101']
['239-245']
['849-855']
['1083-1089']
['1212-1218']
['1371-1377']
['1513-1519']
['2082-2088']
['2122-2128']
['2221-2227']
['2518-2524']
['2700-2706']
['8-29']
['322-333']
['497-508']
['561-572']
['1813-1824']
['3118-3129']
['4075-4086']
['4553-4564']
['4868-4879']
['479-486']
['711-718']
['3098-3105']
['4029-4036']
['3217-3263']
['354-365']
['648-651']
['896-900']
['2

/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/XML/02438044-d6a3-49e9-a1ac-3aad21ef2c8c.xml
['995-1029']
['1030-1040']
['1042-1054']
['1107-1119']
['1042-1054', '1065-1101']
['1125-1132']
['978-987']
['1264-1274']
['1323-1370']
['1379-1395']
['1400-1409']
['1444-1451']
['1476-1495']
['1553-1560']
['1476-1495', '1506-1546']
['1677-1687']
['6187-6197']
['6138-6162']
['5849-5859']
['5902-5942', '5964-5977']
['6352-6362']
['6288-6314']
['6437-6449']
['6425-6435']
['6455-6467']
['6511-6521']
['6541-6574']
['7060-7067']
['7094-7128']
['7323-7354']
['7312-7319', '7333-7354']
['7425-7432']
['9933-9949']
['10273-10298']
['9838-9850']
['9801-9811']
['10032-10044']
['10081-10100', '10111-10151']
['9838-9850', '9860-9896']
['9785-9792']
['10253-10267']
['9986-9995']
['10081-10100']
['10185-10205']
['10218-10227']
['11536-11546']
['11567-11577']
['11703-11713']
['11643-11650']
['11736-11746']
['11811-11821']
['12178-12185']
['12243-12252']
['12307-12316']
['12342-12352']
['12294-12301']




3it [00:00,  4.85it/s]

['17435 17445', '17461 17496']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/Annotations/02438044-d6a3-49e9-a1ac-3aad21ef2c8c.ann
['T38', 'Drug_Class 17502 17522', 'QTc-prolonging drugs']
['17502 17522']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/Annotations/02438044-d6a3-49e9-a1ac-3aad21ef2c8c.ann
['T39', 'IndefinitePronoun 6469 6472', 'all']
['6469 6472']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/Annotations/02438044-d6a3-49e9-a1ac-3aad21ef2c8c.ann
['T40', 'IndefiniteNP 6282 6314', 'three inhibitors of this process']
['6282 6314']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/Annotations/02438044-d6a3-49e9-a1ac-3aad21ef2c8c.ann
['T41', 'DefiniteNP 991 1029', 'the cation transport system inhibitors']
['991 1029']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TRAIN/Annotations/02438044-d6a3-49e9-a1ac-3aad21ef2c8c.ann
['T2', 'Substance 6104 6130', 'the cytochrome P450 system']
['6104 6130']
/home/surya/Documents/bio-coref/Bio-

...

['6867-6878']
['6882-6892']
['6969-6976']
['7020-7028']
['7073-7099']
['7358-7382']
['7563-7570']
['7631-7639']
['7107-7119']
['7121-7133']
['7135-7147']
['7149-7163']
['7165-7175']
['7177-7186']
['7188-7198']
['7200-7210']
['7212-7221']
['7223-7233']
['7238-7251']
['7390-7398']
['7400-7413']
['7415-7424']
['7426-7439']
['7444-7457']
['7896-7907']
['7912-7922']
['7841-7849']
['7937-7968']
['7976-7987']
['7992-8002']
['8150-8157']
['8201-8209']
['8474-8503']
['7753-7772']
None
['108-127']
['2268-2287']
['7327-7341']
['8067-8074']
['8076-8083']
['7816-7827']
['862-869']
['1040-1047']
['4131-4138']
['4316-4323']
['4382-4389']
['7533-7540']
['8413-8426']
['7829-7839']
['26-34']
['87-95']
['202-210']
['324-332']
['443-451']
['693-701']
['762-770']
['781-789']
['879-887']
['1326-1334']
['1522-1530']
['1740-1748']
['2069-2077']
['2289-2297']
['2355-2363']
['2654-2662']
['2709-2717']
['2786-2794']
['3021-3029']
['3681-3689']
['3967-3975']
['3986-3994']
['4174-4182']
['4346-4354']
['4498-4506']


69it [00:10,  5.25it/s]
70it [00:10,  5.91it/s]


['T103', 'Drug 3670 3678', 'TENORMIN']
['3670 3678']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/fcfc9676-4edc-460e-6199-8161b824908f.ann
['T104', 'Drug 3942 3950', 'TENORMIN']
['3942 3950']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/fcfc9676-4edc-460e-6199-8161b824908f.ann
['T105', 'Drug 4352 4360', 'TENORMIN']
['4352 4360']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/fcfc9676-4edc-460e-6199-8161b824908f.ann
['T106', 'Drug 4479 4487', 'TENORMIN']
['4479 4487']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/fcfc9676-4edc-460e-6199-8161b824908f.ann
['T107', 'Drug 5218 5226', 'TENORMIN']
['5218 5226']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/fcfc9676-4edc-460e-6199-8161b824908f.ann
['T108', 'Drug 5342 5350', 'TENORMIN']
['5342 5350']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/fcfc9676-4edc-460e-6199-8161b824908f.ann
['T109', 'Drug 5955 5


72it [00:10,  6.45it/s]


['12657-12666']
['12667-12676']
['12792-12801']
['12876-12885']
['13666-13676']
['13645-13653']
['467-475']
['10346-10354']
['3114-3126']
['3165-3177']
['4229-4241']
['4285-4297']
['4861-4873']
['4885-4897']
['8073-8085']
['11051-11063']
['11107-11119']
['11468-11480']
['12016-12028']
['12040-12052']
['46-55']
['668-677']
['2606-2615']
['5848-5857']
['6603-6612']
['8829-8838']
['9856-9865']
['11277-11286']
['11551-11560']
['12406-12415']
['12505-12514']
['12762-12771']
['12834-12843']
['12989-12998']
['13470-13479']
['13730-13739']
['13922-13931']
['11292-11301']
['184-190']
['690-696']
['8859-8865']
['8923-8929']
['13631-13643']
['10954-10968']
['10621-10628']
['12714-12719']
{}
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/ff61b237-be8e-461b-8114-78c52a8ad0ae.ann
['T3', 'Drug 26 33', 'ADCIRCA']
['26 33']
/home/surya/Documents/bio-coref/Bio-SCoRes/DATA/SPL/TEST/Annotations/ff61b237-be8e-461b-8114-78c52a8ad0ae.ann
['T4', 'Drug_Class 94 110', 'organic nitrates']
[

In [33]:

from allennlp.common import Params
max_span_width = 7
vocab = Vocabulary.from_instances(train_dataset + validation_dataset)
EMBEDDING_DIM = 300
HIDDEN_DIM = 200
FEATURE_SIZE = 20
FEED_HIDDEN = 150
URL = 'https://s3-us-west-2.amazonaws.com/allennlp/datasets/glove/glove.6B.300d.txt.gz'
token_embedding = Embedding.from_params(vocab,Params({'num_embeddings':vocab.get_vocab_size('tokens'),
                            'embedding_dim':EMBEDDING_DIM, 'pretrained_file': URL,\
    "trainable": True}))
text_field_embedder = BasicTextFieldEmbedder({"tokens": token_embedding})
context_layer = PytorchSeq2SeqWrapper(torch.nn.LSTM(EMBEDDING_DIM, HIDDEN_DIM, batch_first=True))
mention_feedforward = allennlp.modules.feedforward.FeedForward(input_dim=720,num_layers=2,hidden_dims=FEED_HIDDEN,activations=torch.nn.functional.relu)
antecedent_feedforward = allennlp.modules.feedforward.FeedForward(input_dim=2180,num_layers=2,hidden_dims=FEED_HIDDEN,activations=torch.nn.functional.relu)
feature_size = FEATURE_SIZE
max_span_width = max_span_width
spans_per_word = 0.4
max_antecedents = 150
lexical_dropout = 0.2

model = CoreferenceResolver(vocab,
                 text_field_embedder,
                 context_layer,
                 mention_feedforward,
                 antecedent_feedforward,
                 feature_size,
                 max_span_width,
                 spans_per_word,
                 max_antecedents,
                 lexical_dropout)

optimizer = optim.Adam(model.parameters(), lr=0.1)
iterator = BucketIterator(batch_size=1, sorting_keys=[("text", "num_tokens")])
iterator.index_with(vocab)
trainer = Trainer(model=model,
                  optimizer=optimizer,
                  iterator=iterator,
                  train_dataset=train_dataset,
                  validation_dataset=validation_dataset,
                  patience=10,
                  num_epochs=1000)
trainer.train()










  0%|          | 0/181 [00:00<?, ?it/s]








 12%|█▏        | 21/181 [00:00<00:00, 207.74it/s]








 27%|██▋       | 49/181 [00:00<00:00, 221.63it/s]








 39%|███▊      | 70/181 [00:00<00:00, 217.88it/s]








 54%|█████▎    | 97/181 [00:00<00:00, 230.48it/s]








 70%|██████▉   | 126/181 [00:00<00:00, 245.52it/s]








 83%|████████▎ | 151/181 [00:00<00:00, 244.74it/s]








 98%|█████████▊| 178/181 [00:00<00:00, 251.68it/s]








100%|██████████| 181/181 [00:00<00:00, 249.06it/s]








0it [00:00, ?it/s]








1249it [00:00, 12489.89it/s]








2777it [00:00, 13213.00it/s]








4178it [00:00, 13438.32it/s]








6082it [00:00, 14737.41it/s]








8327it [00:00, 16427.00it/s]








10846it [00:00, 18340.76it/s]








13494it [00:00, 20202.35it/s]








15800it [00:00, 20981.70it/s]








17942it [00:00, 20448.02it/s]








20546it [00:01, 21852.66it/s]








23234it [00:01, 23147.99it/s]








26244it [00:01, 24867.06it/s]







362020it [00:11, 35539.20it/s]








365620it [00:11, 35675.22it/s]








369196it [00:11, 34481.13it/s]








372761it [00:11, 34818.32it/s]








376254it [00:12, 34818.78it/s]








379744it [00:12, 34776.17it/s]








383227it [00:12, 34733.07it/s]








386704it [00:12, 34344.24it/s]








390142it [00:12, 34258.50it/s]








393720it [00:12, 34688.49it/s]








397204it [00:12, 34733.71it/s]








400000it [00:12, 31311.89it/s]








  0%|          | 0/109 [00:00<?, ?it/s]








coref_precision: 0.0010, coref_recall: 0.0022, coref_f1: 0.0002, mention_recall: 0.0400, loss: 3338.3813 ||:   1%|          | 1/109 [00:09<17:27,  9.70s/it]








coref_precision: 0.0010, coref_recall: 0.0011, coref_f1: 0.0002, mention_recall: 0.0926, loss: 1669.1907 ||:   2%|▏         | 2/109 [00:15<15:12,  8.53s/it]








coref_precision: 0.0010, coref_recall: 0.0009, coref_f1: 0.0001, mention_recall: 0.0909, loss: 1112.7938 ||:   3%|▎         | 3/109 [00:26<16:08,  9.14s/i

KeyboardInterrupt: 